In [12]:
#### specify path of Julia Code for 2D Models ####
### By default the working directory ./2D_Models ###
path = string( pwd(), "/2D_Models/")

"/home/jakob/Dokumente/Repositories/Modeling_Framework/2D_Models/"

In [13]:
##### include 2D Modelling Framework ####
include(string(path, "./2D_model_library.jl"));


########## OPERATIONAL ##########
##### how to chose the actual velocity? #####

#op_model = "Constant"
#op_model = "Collision_Free_Speed"
#op_model = "RVO"
#op_model = "SocialForce"
op_model = "AV_Model"
#op_model = "AV_IN_Model"
#op_model = "PowerLaw"
#op_model = "IN_Costfunction"
#op_model = "IN_Model"
#op_model = "SocialForce"
#op_model = "SocialForce_Elliptical_A"
#op_model = "SocialForce_Elliptical_B"
#op_model = "SocialForce_CollisionPrediction"


include_op_model(op_model, path)

########## TACTICAL ##########
#### how to chose the preferred velocity? ###

#tact_model = "Constant"
tact_model = "IN_Model"

include_tact_model(tact_model, path)


########## STRATEGIC ##########
### how to chose the desired velocity ###

strat_model = "Constant"
#strat_model = "Towards_Goal"
#strat_model = "Two_Goals"

include_strat_model(strat_model, path)


########## OPTIMIZATION SCHEME ##########
### If optimization of a cost-function is included, how to solve? ###

#optimization_scheme = "Regular_Sampling"
optimization_scheme = "Random_Sampling"

include_optimization_scheme(optimization_scheme, path)


##### which update scheme? #####

update = "Parallel_Update"
#update = "Step_Update"

include_update(update, path)


##### which order? i.e. Acceleration or Velocity based? ####
#order = "first"
order = "second"

include_order(order, path)


##### PERCEPTIONAL MODEL ####
perception_model = "None"
#perception_model = "Only_in_Front"

include_perception_model(perception_model, path)

Typical parameters would be:
[2.0, 1.7, 3.0, 0.0, 0.3, 0.0, 0.0, 0.1, 0.0, 5.0, 0.0, 0.0, 0.0, 0.0]
v_max, v_des, T, T2, l, step_time, τ_A, τ_R, α, β, ζ_h, ζ_v, r, λ


In [14]:
#### Special Scenario? ####
x = "Obstacle_Intruder"
#x = "Diminish_ANT_LF"

load_scenario(x, path)

In [24]:
#### parameters of the agents ####
p = [1.0, 0.0, 3.0, 0.0, 0.4, 0.2, 0.0, 0.1, 0.02, 1.0, 0.0, 0.0, 0.5, 0.0]
# ModelParameter: v_max, v_des, T, T2, l, l_min, τ_A, τ_R, α, β, ζ_h, ζ_v, r, ϕ
p_desc = "v_max, v_des, T, T2, l, l_min, τ_A, τ_R, α, β, ζ_h, ζ_v, r, ϕ"

### of the system ###
ρ = 2.0
system_size = (8.0, 4.0) #important for periodic boundaries
N = Int(round(ρ*system_size[1]*system_size[2]))

### of the simulation ###
sim_p = [10.0, 10.0 + 8.0/0.3, 0.05, 0.01, 3.0] #t_relax, t_max, dt_save, dt, r
sim_p_desc = "t_relax, t_max, dt_save, dt, r"

### initialize geometry ###
geometrie = create_geometry_single_obstacle((37.5,31.5), 0.3)

### initialize crowd ###
menge = create_crowd(N, geometrie)

Init_Hom_Parameters!(p, menge)
Init_Hom_Vels!(menge, 0.1)
Init_E_des!(menge, (1.0, 0.0))

initialize_random_positions(system_size, menge, geometrie)
#CrowdOneSide!(menge, 0.5, 0.0, 4.0)
#Init_Homogeneous_Random_InitialPositions_INTRUDER(menge, geometrie, system_size, 1.0)

Init_Random_Headings!(menge)

vel, l_obs, l_min_intr = 0.3, 0.8, 0.6
Init_Nth_Agent_as_Moving_Obstacle!(menge, system_size, l_obs, l_min_intr, vel);

In [25]:
positions, headings = Simulate!(menge, geometrie, sim_p[1], sim_p[2], sim_p[3], sim_p[4], sim_p[5], system_size);

In [26]:
using GR
GR.inline("mov")

j = 1

dt_save = sim_p[3]
geometry_x, geometry_y = rewrite_geometry(geometrie)
boundaries_x, boundaries_y = boundaries_rectangle_positions(system_size)

while j*sim_p[3] < sim_p[2]-sim_p[1]
    
        GR.clearws()

        GR.setwindow(-1, 11, -1, 11)
        GR.setviewport(0.0, 1, 0.0, 1)
    

        plot_boundaries(boundaries_x, boundaries_y, 0.2, 999)        
        plot_geometry(geometry_x, geometry_y, 3.7, 20)

        plot_agents(positions[j, 1:N-1], headings[j, 1:N-1], 2.3, 100, 0.7, 999, 0.1)
    
        #plot moving obstacle
        plot_agents(positions[j, N:end], headings[j, N:end], 3.7, 97, 0.0, 999, 0.1)

        model = op_model
        timer = string("time ", round(j*dt_save, digits = 1), "s")
        GR.text(0.5, 0.95, timer)
        GR.text(0.5, 0.9, model)
        
        GR.updatews()
    
        j = j+1
end

In [27]:
GR.show()

GR.HTML("<video autoplay controls><source type=\"video/mp4\" src=\"data:video/mp4;base64,AAAAFGZ0eXBxdCAgAAACAHF0ICAAAAAId2lkZQAiqpltZGF0AAACsQYF//+t3EXpvebZSLeWLNgg2SPu73gyNjQgLSBjb3JlIDE2MyAtIEguMjY0L01QRUctNCBBVkMgY29kZWMgLSBDb3B5bGVmdCAyMDAzLTIwMjEgLSBodHRwOi8vd3d3LnZpZGVvbGFuLm9yZy94MjY0Lmh0bWwgLSBvcHRpb25zOiBjYWJhYz0xIHJlZj0zIGRlYmxvY2s9MTowOjAgYW5hbHlzZT0weDM6MHgxMTMgbWU9aGV4IHN1Ym1lPTcgcHN5PTEgcHN5X3JkPTEuMDA6MC4wMCBtaXhlZF9yZWY9MSBtZV9yYW5nZT0xNiBjaHJvbWFfbWU9MSB0cmVsbGlzPTEgOHg4ZGN0PTEgY3FtPTAgZGVhZHpvbmU9MjEsMTEgZmFzdF9wc2tpcD0xIGNocm9tYV9xcF9vZmZzZXQ9LTIgdGhyZWFkcz0xMiBsb29rYWhlYWRfdGhyZWFkcz0yIHNsaWNlZF90aHJlYWRzPTAgbnI9MCBkZWNpbWF0ZT0xIGludGVybGFjZWQ9MCBibHVyYXlfY29tcGF0PTAgY29uc3RyYWluZWRfaW50cmE9MCBiZnJhbWVzPTMgYl9weXJhbWlkPTIgYl9hZGFwdD0xIGJfYmlhcz0wIGRpcmVjdD0xIHdlaWdodGI9MSBvcGVuX2dvcD0wIHdlaWdodHA9MiBrZXlpbnQ9MjUwIGtleWludF9taW49MjQgc2NlbmVjdXQ9NDAgaW50cmFfcmVmcmVzaD0wIHJjX2xvb2thaGVhZD00MCByYz1hYnIgbWJ0cmVlPTEgYml0cmF0ZT00MDAwIHJhdGV0b2w9MS4wIHFjb21wPTAuNjAgcXBtaW49MCBxcG1heD02OSBxcHN0ZXA9NCBpcF9yYXRpbz0xLjQwIGFxPTE6MS4wMACAAABuumWIhAAa//731LfMsu1Tb7YLqPeiniZfQ3UlAZuWxO06gAAAAwAAAwAAAwDpVIJjfO4A0Yy0DR+f2K4gDKdDocQKtjRy1EiAtdMSFpyuZYRVM6X0NlJ+oA8lHGo38VmUH95MU0d89tuB5s0Td5MylSissVBdG75/oP/3h/4+iG23qzuIA9SnVmc0e+25bbL5As4EO8db8eR4h2qSGs9U1eaXQKOQdHk/04vErZS5iwMOpop0GfsV+NlEAwDNeMst0csxcxQEiyOvirfAsRUoKvGId/kiC+3+1f27cWxh9qekVLJwDSk01BzOomvNBnCeVYx21viXJ7QDd9E2xJ0jRnnEuXAImMtKzedGYBW0DNW81d51UGbRvxruLmyf5szeYJBoFU7UZZ4CEiX6jBRS74LUSeNendbI50S4tU94PdBqv/vf4Q7d6vXjQmS5GxuwXA1J3HGfP/acP5BLOg+wSjTslSdVhQ092kDj2qRFAqnsWlah0HWkSNd+LMDTmPD7Vqf4zduEfC+7lIQCsrdknPL8n7S8364CCcEQopSuNguXiFSl1Rf7KE40QlbAFCFYFPCKDSrc+FiDLkhHDE4BFp7Kw+dfaXEkv36wh2dL+X99zO+k0Tg+Zrs/5Ys7t8oJdIKHhi2368PcFvYfWtfu9Ehsqn8xlqGJtUw9nhxFNOPfPJ0HhFJvsbf3o/LZ/fWHuK1r5+ln9s8S3JnLxIA/w+vI9kudhxcOUdiU93OEtoj7ra6FOfWFsH87+rRslaD75PDn4DgfQbLWtXz9m6KGAGdmdnQ4TopDhIfOBDjhOLW5EDmwjPJ33qRNzHtJcN4zj6zyuS7HeI8gjzniYPTCJBzRpj6sgWA3geC53yvallNnVmkH+m0slVaZQS2KJarOKT4G/MFkt/wYE0Jg6u+jwHodcch0bUgK5Ex937gdcGbV3zmkWeRjXxo98Y6rRrNgTthj1gwHzTYUPSpP/nFXhBWIJR0Nqd6vqskZM5E06H/X5/jLZNumB/VUAwjesbUox+LQJLb+T0MGk/amaCVRSFdhLl+konwySuYTxtkr1NGBX0dd/5dZwvnvy4y1z6DkS0B4oXnu9ZTCDwgA6AD3HfWt+zCdbL5wY+L2C75P1YTAHVqc/qIt+B0x9ftNPfufyHZrkD/8f9i6r+7nA1ht0qQx7/9q7x6SFMC1QVKQe3IPCSfjsfqUCFSm6yOCFWgp4bIoh5MFllvgGxxQlSagrxeSgQNysWu81TxieJ5WTpXWoW1N0j4LxS0bwFqiXryOt/UlZYwpsn7mh1zYBCLh9B+jgz0crbVKQHvgj6TIdaztyxpD1pS8sUveOCviW+QtoP6evvvbAv/r2uJ4rxGW1Jw8EF+NvlL9n4KOF4w+tASLuJ8JgxmLnV0p5fOwDyg5zy302NfBR7lxGyw9XJ07H+ErYNw8NsbyHEXfHLTwNAqlzgYQ11SQJoHRUwhnG3T6B2ZMWCJPpNwWaPBoarqVEJs7XyrIItKOYjljfY62wAzE1QPobQJTWAOljmQOcNsGPhXTLVY7gqgBZpTQWSgQQN5KHolNLnc9DMvZbn6mduy1P+0Aaip/tuLrA0b9kAolxzn33YQWk7CSIf0yM6w5N1RXuNODu4qzQamL8617vD3J4azm28vGJSiDK/8FGReXK7+gbWpPplrGBzQG9AAzqJzJMdnvFa6Qy46vEoYEN/LbT6dkJZgPLbbkss31W8wFXiGouP++DRdpOPqJqk6AVRqfOHML4Onu8Zg3gncnEKKyASKyLyvpSsZYvoFKRTcFMrv1twl/zgjVXo/eK0ckLRD4PSFoLS22gJ6FjM0Ficowu6K5oCWtspTkjwMgq/06zh969ki8kfktGmLHVsqbq3m8qM2Doj8priSkduuFqKpq0i/29Pm5IRvmmKf0fU1SEBJ0Pn6U48fSGlsVg8/K8Y6jGlx4IR7E1Coo58SmFch6mJ8Ggny1T0WdwZd+dlyyUydGm+Vilrv1znkzc4mFuddDwjRMz/3drwFa9xueMMBDVcBs/fCVXpAzmRGH7YNTl3Jl/GSHmZl1DxnCljE0JpjLoJjjvhQ9PjnRnupEuZTf21R+hLAi7sh4c9J8se5DjvBhzItaBVD/OilFQxblaYvBUcCtfN2+LT+0SDNvuStZWmWS/01kLjzSB1QYigF42AALr7kXP8XNheA4IZ9S4h3A+5eD/+xKjbDqoMrwRm7Gyhb/RhberC9PmfKyhR/0ayDPQblBYeruwBidXi5LIx0E/T/9cPMT9maWY8JVnNCOZksGTj/C/UmqZFl/jKCx2Yma/QS92KxykBcf72VkNc3+kgXIaxhbVNN6OaKXEuuLjHqmrTWQpVuUjm0CIprklxZnsJhHa0z1XA6gvvDQUVVp9M1IRNr6TQBKKBvImJT2/qbHOFazdvi2DDs7Rp1YHyHOT9Qcd8bm0ShiObfjk/HPNgUvWtvAVE4cCb8rmB4WmKIGkJn16kcFLxZVl9u1DeYs0P7FXy7+0by9A4K9hqu2j32D0iYTUNCr3jeLqeqT8GPSs8v6I3FW1KH/8VJ1UyOHr1oDtqPPkiUrneYamaHUbghiP43SUaBu9fuu+i9ieWuYMVm56o6vnTROppcEUtuxg+kw8a7EskKUjwo3A0vbIE2bYrYNpvVDzT7za8HT1DO0o7eu4Dx3ZBJTplhqSMb0fOy1V7Tfdw+7MZI//i52aRunIYNho3amaPsTwCL0Xkkm7jR0bTgmm9LYGw4DnGsKkuHPzMY02E7YVhhGq5GJaAJl5NvKCPY136Otiye3gpJ0gimeI1Lc1fHaLazNA7GYaUSbhq1O03QFKZnwU/2Xw2nQ/xikkRyzwL5MAo02JYn4hDYI+QvVXfJmLCraVA7rhjJfjQ5N4D6CWs5+nl7X0CwN7z6fQUcXhnUu1ph/kYtYIHCYywn

In [15]:
Path = "/home/jakob/Dokumente/Sim_Data/"
dir = "Intruder_AV_IN_SingleAgent" 
header = Header(p, p_desc, sim_p, sim_p_desc, op_model, tact_model, order, update, N, system_size);

Save_Data!(Path, dir, header, positions)

Created Directory /Intruder_AV_IN_SingleAgent.


In [16]:
samples = 500

for i in 1:samples
    
    Random.seed!()
    
    #if mod(i, 10) == 0
        println(i)
    #end
    
    initialize_random_positions(system_size, menge, geometrie)
    #CrowdOneSide!(menge, 0.5, 0.0, 4.0)
    #Init_Homogeneous_Random_InitialPositions_INTRUDER(menge, geometrie, system_size, 0.25)

    Init_Random_Headings!(menge)
    vel, l_obs = 0.3, 0.7

    Init_Nth_Agent_as_Moving_Obstacle!(menge, system_size, l_obs, vel);
    
    positions, headings = Simulate!(menge, geometrie, sim_p[1], sim_p[2], sim_p[3], sim_p[4], sim_p[5], system_size);
    Save_Data!(Path, dir, header, positions)
    
end

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277
